# מדע הנתונים בענן: הדרך של "Azure ML SDK"

## הקדמה

במחברת זו נלמד כיצד להשתמש ב-Azure ML SDK כדי לאמן, לפרוס ולצרוך מודל באמצעות Azure ML.

דרישות מקדימות:
1. יצרתם סביבת עבודה של Azure ML.
2. טעינתם את [מאגר הנתונים של אי ספיקת לב](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) ל-Azure ML.
3. העליתם את המחברת הזו ל-Azure ML Studio.

השלבים הבאים הם:

1. יצירת ניסוי בסביבת עבודה קיימת.
2. יצירת אשכול חישוב.
3. טעינת מאגר הנתונים.
4. הגדרת AutoML באמצעות AutoMLConfig.
5. הרצת ניסוי AutoML.
6. חקר התוצאות וקבלת המודל הטוב ביותר.
7. רישום המודל הטוב ביותר.
8. פריסת המודל הטוב ביותר.
9. צריכת נקודת הקצה.

## ייבוא ספציפי ל-Azure Machine Learning SDK


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## אתחול סביבת עבודה  
אתחל אובייקט סביבת עבודה מתוך קובץ תצורה שמור. ודא שקובץ התצורה נמצא ב-.\config.json  


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## יצירת ניסוי ב-Azure ML

בואו ניצור ניסוי בשם 'aml-experiment' בסביבת העבודה שהרגע יצרנו.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## יצירת אשכול חישוב  
תצטרכו ליצור [יעד חישוב](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target) עבור הרצת AutoML שלכם.  


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## נתונים  
ודא שהעלית את מערך הנתונים ל-Azure ML ושמפתח השם זהה לשם מערך הנתונים.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

## תצורת AutoML


In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

## הפעלת AutoML


In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## פריסת המודל הטוב ביותר

הרץ את הקוד הבא כדי לפרוס את המודל הטוב ביותר. ניתן לראות את מצב הפריסה בפורטל Azure ML. שלב זה עשוי לקחת כמה דקות.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## שימוש בנקודת הקצה
ניתן להוסיף קלטים לדוגמת הקלט הבאה.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**כתב ויתור**:  
מסמך זה תורגם באמצעות שירות תרגום מבוסס בינה מלאכותית [Co-op Translator](https://github.com/Azure/co-op-translator). בעוד שאנו שואפים לדיוק, יש להיות מודעים לכך שתרגומים אוטומטיים עשויים להכיל שגיאות או אי דיוקים. המסמך המקורי בשפתו המקורית צריך להיחשב כמקור סמכותי. עבור מידע קריטי, מומלץ להשתמש בתרגום מקצועי על ידי אדם. איננו נושאים באחריות לאי הבנות או לפרשנויות שגויות הנובעות משימוש בתרגום זה.
